<a href="https://colab.research.google.com/github/mohammadbadi/Clustering_Frequency/blob/main/Code%20Sections/5.7%20Clustering%20Model%20Training.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### **5.7 Clustering Model Training - Approach 2**

In [ ]:
import warnings
import ast
import numpy as np
import pandas as pd
import time
from sklearn.cluster import KMeans, DBSCAN
from sklearn.metrics import silhouette_score, davies_bouldin_score, calinski_harabasz_score
from sklearn.preprocessing import StandardScaler
from IPython.display import display, HTML
from google.colab import files

print("\n\n")
warnings.filterwarnings("ignore", category=DeprecationWarning)                    # Ignore Deprecation Warnings
warnings.filterwarnings("ignore", category=FutureWarning)                         # Ignore future warnings
combos_url = "https://raw.githubusercontent.com/mohammadbadi/Clustering_Frequency/refs/heads/main/Output_CSV/Feature_Combos__Freq_New.csv"  # URL of the csv file with all Combinations of Features
combos_df = pd.read_csv(combos_url)                                               # Read ALL feature combinations from URL
                                                                                  # Display message that feature sets have been read
display(HTML("<p style='color: green; font-size:16px;'><b>Feature combination specifications loaded from 'Feature_Combos__Freq_New.csv'</b></p>"))
                                                                                  # Read the dataset from the new URL
data_url = "https://raw.githubusercontent.com/mohammadbadi/Clustering_Frequency/refs/heads/main/Output_CSV/FE_Encoded_New.csv"
data = pd.read_csv(data_url)
sample_data = data.sample(frac=0.1, random_state=42)                              # Sample 10% of the data for clustering
results = {}                                                                      # Track results - to store clustering metrics for each feature set
total_models = 0

def color_silhouette(value):
    """Color code Silhouette Score (higher is better)"""
    if value >= 0.6:
        color = "#32cd32"                                                         # green
    elif value >= 0.3:
        color = "#ffcc00"                                                         # yellow
    else:
        color = "#ff6347"                                                         # red
    return f"<span style='color: {color}; font-weight: bold;'>{value:.2f}</span>"

def color_dbi(value):
    """Color code Davies-Bouldin Index (lower is better)"""
    if value <= 1.0:
        color = "#32cd32"                                                         # green
    elif value <= 1.5:
        color = "#ffcc00"                                                         # yellow
    else:
        color = "#ff6347"                                                         # red
    return f"<span style='color: {color}; font-weight: bold;'>{value:.2f}</span>"

def color_accuracy(value):
    """Color code prediction accuracy: below 50% red, 50.1%+ green"""
    if value < 50.1:
        color = "#ff6347"                                                         # red
    else:
        color = "#32cd32"                                                         # green
    return f"<span style='color: {color}; font-weight: bold;'>{value:.2f}%</span>"
                                                                                  # Iterate through each feature set from the combination file
for idx, row in combos_df.iterrows():
    total_models += 1
    set_number = row['set_number']
                                                                                  # Convert the string representation of features into an actual list
    feature_set = ast.literal_eval(row['features'])
                                                                                  # Round best_eps to one decimal place
    best_eps = round(row['best_eps'], 1)
    best_min_samples = row['best_min_samples']

    valid_features = [f for f in feature_set if f in sample_data.columns]         # Ensure features exist in the dataset
    if len(valid_features) != len(feature_set):
        print(f"Warning: Some features in {feature_set} are missing. Using only: {valid_features}")

    data_for_clustering = sample_data[valid_features]
    numerical_cols = data_for_clustering.select_dtypes(include=['int64', 'float64']).columns.tolist()  # Standardize numerical columns
    scaler = StandardScaler()
    data_scaled = pd.DataFrame(scaler.fit_transform(data_for_clustering[numerical_cols]), columns=numerical_cols)
    categorical_cols = [col for col in valid_features if col not in numerical_cols]  # Append any categorical columns
    if categorical_cols:
        data_scaled = pd.concat([data_scaled, data_for_clustering[categorical_cols]], axis=1)
                                                                                  # Perform KMeans clustering with n_clusters=4
    kmeans = KMeans(n_clusters=4, random_state=42)
    kmeans_labels = kmeans.fit_predict(data_scaled)
                                                                                  # Perform DBSCAN clustering with eps and min_samples from the feature combo file
    dbscan = DBSCAN(eps=best_eps, min_samples=best_min_samples)
    dbscan_labels = dbscan.fit_predict(data_scaled)
                                                                                  # Calculate clustering metrics for KMeans
    silhouette_kmeans = silhouette_score(data_scaled, kmeans_labels)
    dbi_kmeans = davies_bouldin_score(data_scaled, kmeans_labels)
    ch_kmeans = calinski_harabasz_score(data_scaled, kmeans_labels)
    kmeans_accuracy = max(0, silhouette_kmeans) * 100
                                                                                  # Calculate clustering metrics for DBSCAN (if possible)
    silhouette_dbscan = -1 if len(set(dbscan_labels)) <= 1 else silhouette_score(data_scaled, dbscan_labels)
    dbi_dbscan = -1 if len(set(dbscan_labels)) <= 1 else davies_bouldin_score(data_scaled, dbscan_labels)
    dbscan_accuracy = max(0, silhouette_dbscan) * 100

    num_features = len(valid_features)
    formatted_features = [f"'{feature}'" for feature in valid_features]
    feature_names_string = f"[{', '.join(formatted_features)}]"

    results[tuple(valid_features)] = {
        'Set Number': set_number,
        'Number of Features': num_features,
        'Features': feature_names_string,
        'KMeans Silhouette Score': silhouette_kmeans,
        'KMeans Davies-Bouldin Index': dbi_kmeans,
        'KMeans Calinski-Harabasz Score': ch_kmeans,
        'KMeans Prediction Accuracy': kmeans_accuracy,
        'DBSCAN Silhouette Score': silhouette_dbscan,
        'DBSCAN Davies-Bouldin Index': dbi_dbscan,
        'DBSCAN Prediction Accuracy': dbscan_accuracy,
        'Best eps': best_eps,
        'Best min_samples': best_min_samples
    }
                                                                                  # Create HTML table output for the current result
    results_html = f"""
    <div style="margin: 10px auto; width: 80%; border: 2px solid #ddd; padding: 10px; background-color: #f9f9f9;">
      <table style="width: 100%; border-collapse: collapse; text-align: center;">
        <tr>
          <th colspan="3" style="font-size: 14px; padding: 10px; text-align: left;">Result of Set {set_number}</th>
        </tr>
        <tr>
          <th colspan="3" style="font-size: 13px; padding: 5px; text-align: left;">Number of Features: {num_features} &nbsp;&nbsp;&nbsp; | &nbsp;&nbsp;&nbsp; Features in this model: {feature_names_string}</th>
        </tr>
        <tr style="background-color: #e0e0e0; font-weight: bold;">
          <td style="padding: 8px; border: 1px solid #ddd;">Statistic</td>
          <td style="padding: 8px; border: 1px solid #ddd;">KMeans</td>
          <td style="padding: 8px; border: 1px solid #ddd;">
            DBSCAN<br>
            <span style="font-size: small;">(eps: {best_eps:.1f}, min_samples: {best_min_samples})</span>
          </td>
        </tr>
        <tr>
          <td style="padding: 8px; border: 1px solid #ddd;">Silhouette Score</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{color_silhouette(silhouette_kmeans)}</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{"N/A" if silhouette_dbscan == -1 else color_silhouette(silhouette_dbscan)}</td>
        </tr>
        <tr>
          <td style="padding: 8px; border: 1px solid #ddd;">Davies-Bouldin Index</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{color_dbi(dbi_kmeans)}</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{"N/A" if dbi_dbscan == -1 else color_dbi(dbi_dbscan)}</td>
        </tr>
        <tr>
          <td style="padding: 8px; border: 1px solid #ddd;">Calinski-Harabasz Score</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{round(ch_kmeans,2)}</td>
          <td style="padding: 8px; border: 1px solid #ddd;">-</td>
        </tr>
        <tr style="font-weight: bold;">
          <td style="padding: 8px; border: 1px solid #ddd;">Prediction Accuracy</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{color_accuracy(kmeans_accuracy)}</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{color_accuracy(dbscan_accuracy)}</td>
        </tr>
      </table>
    </div>
    """
    display(HTML(results_html))
    time.sleep(0.1)

results_df = pd.DataFrame(results.values())
results_df.to_csv('Feature_Combo_New_Results.csv', index=False)
files.download('Feature_Combo_New_Results.csv')
                                                                                  # Display formatted message for saved file
display(HTML("""
    <p style="color: darkblue; font-size: 18px; font-weight: bold;">
         Results have been saved as <span style="color: green;">Feature_Combo_New_Results.csv</span>.
    </p>
"""))
display(HTML(f"<h2 style='color: navy; font-size:18px;'><b>Total K-Means & DBSCAN Clustering Models Trained: {total_models}</b></h2>"))
print("\n\n")
display(HTML(f"""
<div style="font-family: Arial, sans-serif; font-size: 18px; padding: 15px; border-radius: 10px;
             background: #282c34; color: #61dafb; text-align: center; width: 60%; margin: 20px auto;
             box-shadow: 2px 2px 10px rgba(0,0,0,0.2);">
    <strong>Total K-Means & DBSCAN Clustering models trained:</strong>
    <span style="color: #ffcc00; font-size: 22px;">{total_models}</span>
</div>
"""))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>